In [3]:
from datetime import timedelta
import pandas as pd
import json
import requests
import numpy as np

import itertools

from datetime import date, timedelta
import plotly.express as px
from plotly.subplots import make_subplots
import datetime as dt

import math
import time

import haversine

%reload_ext autoreload
%autoreload 2

import plotly.graph_objects as go

import sys
sys.path.append('..')
from src.co2_modells import co2_modell, co2_modell_direct
from src.data_matrix import create_dict_points, create_df_distance_matrix
from src.data_for_tool import data_import, create_limited_dataset, remove_nan_distance_matrix
from src.plots import show_clients, show_clients_dc, show_clients_per_dc, show_clients_per_dc_and_both, template
from src.data_matrix import get_distance_osrm_dc_clients, create_dict_points
from src.create_solution import create_df_analysis_150_20
from src.data_for_tool import data_for_tool, create_table_daily_mean, create_table_total, create_lists_days_weeks_months
import plotly.io as pio
pio.templates.default = template
from src.plots import poi_poly

from src.co2_modells import co2_modell_direct

from src.distance import get_waypoints_osrm

In [4]:
# maybe legend inside
# Farbgebung und font anpassne

In [5]:
def outlier_removal(dummy_df, cols):
    q1 = dummy_df[cols].quantile(0.25) # Same as np.percentile but maps (0,1) and not (0,100)
    q3 = dummy_df[cols].quantile(0.75)
    iqr = q3 - q1
    upper_limit = (q3+1.5*iqr)
    lower_limit = (q3-1.5*iqr)
    print(upper_limit, lower_limit)
    # Filter our dataframe based on condition
    filtered_df = dummy_df[(dummy_df[cols] < upper_limit)&(dummy_df[cols] > lower_limit)]
    return filtered_df

import scipy.stats as stats
def outlier_removal_z(col):
    #find absolute value of z-score for each observation
    z = np.abs(stats.zscore(col))
    idx_non_outliers = np.where(z<3, True, False)
    return pd.Series(idx_non_outliers, index = col.index)

In [6]:
list_days, list_mondays, list_bi_daily, list_months = create_lists_days_weeks_months(2022)

# Data Import

In [52]:
df, df_terminal, dict_terminals = data_import()
# df["Sender weight (kg)"] = df["Sender weight (kg)"]*2

C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code_New\notebooks\..\src\data_for_tool.py:161: DtypeWarning:

Columns (1,5,14) have mixed types. Specify dtype option on import or set low_memory=False.



In [53]:
old_weight = df["Sender weight (kg)"].sum()

In [27]:
show_clients_dc(df, "output/plots/show_clients_dc.html")
show_clients_per_dc(df, "output/plots/show_clients_per_dc.html")
show_clients_per_dc_and_both(df, "output/plots/show_clients_per_dc_and_both.html")

C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\plots.py:348: FutureWarning:

The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.

C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\plots.py:368: FutureWarning:

The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.

C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\plots.py:386: FutureWarning:

The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.



### only France mainland

In [54]:
# Scope only France mainland
# Corsica filter
df = df[~((df["Receiver longitude"]>7)&(df["Receiver latitude"]<43))]
# Spanien filter
df = df[~((df["Receiver longitude"]<0)&(df["Receiver latitude"]<41))]
df = df[df["Receiver name"]!="C4460"]
df = df[df["Receiver name"]!="C1454"]
df = df[df["Receiver name"]!="C758"]

In [55]:
df = df.drop_duplicates()

In [56]:
len(df["Receiver name"].unique())

8580

In [31]:
show_clients_dc(df, "output/plots/show_clients_dc_mainland.html")
show_clients_per_dc(df, "output/plots/show_clients_per_dc_mainland.html")
show_clients_per_dc_and_both(df, "output/plots/show_clients_per_dc_and_both_mainland.html")

C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\plots.py:348: FutureWarning:

The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.

C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\plots.py:368: FutureWarning:

The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.

C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\plots.py:386: FutureWarning:

The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.



### Outlier removal with IQR

In [11]:
# Outlier removal with IQR
def plot_outlier_removal(df, path_plot = False):
    fig = go.Figure()
    fig.add_trace(go.Box(x = df["Sender weight (kg)"], name = "All points"))
    df = outlier_removal(df, "Sender weight (kg)")
    fig.add_trace(go.Box(x = df["Sender weight (kg)"], boxpoints = False, name = "After removal"))
    fig.update_layout(xaxis_title='Sender weight (kg)')
    if path_plot == False:
            fig.show()
    else:
        fig.write_html(path_plot, auto_open = False)
    return df

In [57]:
df = plot_outlier_removal(df, "output/plots/plot_outlier_removal.html")

48.353125000000006 -8.086625000000002


## Data Exploration

In [13]:
def boxplot_distribution(df, path_plot = False):
    fig = go.Figure()
    fig.add_trace(go.Box(x = df[df["Shipper name"]=="DC2"]["Sender weight (kg)"], name = "DC2"))
    fig.add_trace(go.Box(x = df[df["Shipper name"]=="DC1"]["Sender weight (kg)"], name = "DC1"))
    fig.add_trace(go.Box(x = df["Sender weight (kg)"],  name = "both DCs"))
    fig.update_traces(boxpoints = False)
    fig.update_layout(xaxis_title='Sender weight (kg)')
    if path_plot == False:
            fig.show()
    else:
        fig.write_html(path_plot, auto_open = False)

In [114]:
boxplot_distribution(df)

In [35]:
boxplot_distribution(df, "output/plots/boxplot_distribution.html")

In [58]:
df = df[df["Sender weight (kg)"]>1]

In [37]:
len(df["Receiver name"].unique())

7305

### 80% Rule

In [38]:
def plot_80_20_rule(data, dc, path_plot = False):
    title_font=dict(size=12)
    fig = make_subplots(rows=2, cols=1, shared_xaxes=True,vertical_spacing=0.05, row_heights = [0.5, 0.5])
    df_dc = data[data["Shipper name"]==dc]
    df_dc["Sender weight (kg)"] = df_dc["Sender weight (kg)"]/1000

    weight = df_dc.groupby(["Receiver name"])["Sender weight (kg)"].sum().reset_index().sort_values(by = "Sender weight (kg)", ascending=False).reset_index()
    weight["Sender weight cum"] = weight["Sender weight (kg)"].cumsum()

    # Row 1
    fig.add_trace(go.Scatter(x = weight.index, y = weight["Sender weight (kg)"], name = "weight per client"), row = 1, col = 1)
    fig.update_yaxes(title_text = "Sender weight (t)", row = 1, col = 1)

    # Row 2
    fig.add_trace(go.Scatter(x = weight.index, y = weight["Sender weight cum"]), row = 2, col = 1)
    x_add = 0
    for i in [0.8,0.9,1]:
        y1 = df_dc["Sender weight (kg)"].sum()*i
        x1 = len(weight[weight["Sender weight cum"]<df_dc["Sender weight (kg)"].sum()*i].index)
        print(x1)
        fig.add_shape(type = "rect", y0=0, y1=y1, x0 = 0, x1 = x1, line_width=0, fillcolor="red", opacity=0.2, row = 2, col = 1)
        fig.add_trace(go.Scatter(x=[(x1+x_add)/2],y=[y1/2],text=[f"{i*100:.0f}%"],mode="text"), row = 2, col = 1)
        x_add = x1
    fig.update_xaxes(
        #showticklabels=False, 
        title = "Number of clients sorted by sender weight", row = 2, col = 1)
    fig.update_yaxes(title = "Cumulated<br>sender weight (t)", row = 2, col = 1)
    fig.update_traces(showlegend = False)
    fig.update_yaxes(title_font=title_font)
    fig.update_xaxes(title_font=title_font)
    fig.update_layout(height = 800)
    if path_plot == False:
            fig.show()
    else:
        fig.write_html(path_plot, auto_open = False)

In [39]:
plot_80_20_rule(df, "DC1", "output/plots/boxplot_distribution_dc1.html")
plot_80_20_rule(df, "DC2", "output/plots/boxplot_distribution_dc2.html")

C:\Users\marle\AppData\Local\Temp\ipykernel_16580\3376088496.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



522
893
5211
567
1090
4608


C:\Users\marle\AppData\Local\Temp\ipykernel_16580\3376088496.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



### Final dataset and distance matrix

In [83]:
# Limited dataset
df_limited = pd.concat([create_limited_dataset(df, 0.8, "DC1"), create_limited_dataset(df, 0.8, "DC2")])
len(df_limited["Receiver name"].unique())

517
558


776

> Cleaning done

#### df distance matrix

In [35]:
df_distance_matrix = create_df_distance_matrix(df_limited_dc1, dict_terminals)

1
2
3
4
5
6
7
8
9


In [42]:
#df_distance_matrix.to_csv("results/df_distance_matrix.csv")

In [66]:
dict_points = create_dict_points(df_limited, "Shipper name", "Shipper latitude", "Shipper longitude")       
dict_points.update(create_dict_points(df_limited, "Receiver name", "Receiver latitude", "Receiver longitude"))
dict_points.update(dict_terminals)
# with open("../data/processed/dict_points.json", "w") as fp:
#     json.dump(dict_points , fp) 

In [32]:
# with open("../data/processed/dict_points.json", "w") as fp:
#     json.dump(dict_points , fp) 

NameError: name 'dict_points' is not defined

In [74]:
df_distance_matrix = pd.read_csv("results/df_distance_matrix.csv", index_col = 0)

#### final dataset

In [45]:
df_limited.to_csv("results/df_limited.csv", index = False)

## Terminals 

In [47]:
def show_terminals_150(dict_terminals, path_plot = False):
    list_dict_circle = [{
        "source": json.loads(
            poi_poly(None, poi={"Latitude": dict_terminals[i][0],"Longitude": dict_terminals[i][1]}, 
                     radius=150000).to_json()),
        "below": "traces",
        "type": "fill",
        "color": "green",
        "line": {"width": 1.5},
        "opacity": 0.2
        #"fillcolor": "red"
        } for i in dict_terminals.keys()]

    fig = go.Figure()
    fig.add_trace(go.Scattermapbox(lat=[i[0] for i in list(dict_terminals.values())], lon=[i[1] for i in list(dict_terminals.values())], 
                                   mode = 'markers', marker = {'size': 12, "color": "green"}, name = f"Terminals"))
    fig.update_layout(margin={"r": 0, "t": 40, "l": 0, "b": 40}, mapbox={
                      'zoom': 4, "center": {'lat': 45, 'lon': 3}})
    fig.update_layout(mapbox={
                "style": "open-street-map",
                "layers": list_dict_circle
            })
    fig.update_layout(height = 500)
    if path_plot == False:
        fig.show()
    else:
        fig.write_html(path_plot, auto_open = False)

In [48]:
def show_clients_terminals_150(df, dict_terminals, path_plot = False):
    dict_colors = {
        "No": "green",
        "Yes": "red",
        "Road": "blue"
    }
    dict_legend = {
        "No": "with suitable terminal",
        "Yes": "with no suitable terminal",
        "Road": "assigned to allroad"
    }
    list_dict_circle = [{
        "source": json.loads(
            poi_poly(None, poi={"Latitude": dict_terminals[i][0],"Longitude": dict_terminals[i][1]}, 
                     radius=150000).to_json()),
        "below": "traces",
        "type": "fill",
        "color": "green",
        "line": {"width": 1.5},
        "opacity": 0.2
        #"fillcolor": "red"
        } for i in dict_terminals.keys()]
    dict_points = create_dict_points(df, "Shipper name", "Shipper latitude", "Shipper longitude") 
    dict_points.update(create_dict_points(df, "Receiver name", "Receiver latitude", "Receiver longitude"))
    df_150_20 = create_df_analysis_150_20(df, dict_terminals, dict_points)
    
    df = df.merge(df_150_20[["More than 150km"]].reset_index(names = "Receiver name"), 
                                  on = ["Receiver name"], how = "left")
    fig = go.Figure()
    for i in list(df["More than 150km"].unique()):
        df_temp = df[(df["More than 150km"]==i)]
        fig.add_trace(go.Scattermapbox(lat=df_temp['Receiver latitude'].to_list(), lon=df_temp['Receiver longitude'].to_list(), 
                                   mode = 'markers', marker = {'size': 4, 'color': dict_colors[i]}, name = f"Clients {dict_legend[i]}",
                                   customdata=df_temp[["Receiver name", "Sender weight (kg)"]],
                                   hovertemplate='''<br>%{customdata[0]}: %{customdata[1]}kg<br><extra></extra>'''))
    fig.add_trace(go.Scattermapbox(lat=[i[0] for i in list(dict_terminals.values())], lon=[i[1] for i in list(dict_terminals.values())], 
                                   mode = 'markers', marker = {'size': 12}, name = f"Terminals"))
    fig.add_trace(go.Scattermapbox(lat=[df["Shipper latitude"].iloc[0]], lon=[df["Shipper longitude"].iloc[0]], 
                                   mode = 'markers', marker = {'size': 12}, name = f'{df["Shipper name"].iloc[0]}'))
    fig.update_layout(margin={"r": 0, "t": 40, "l": 0, "b": 40}, mapbox={
                      'zoom': 4, "center": {'lat': 45, 'lon': 3}})
    fig.update_layout(legend=dict(
        yanchor="top",
        y=0.99,
        xanchor="left",
        x=0.01
    ))
    fig.update_layout(mapbox={
                "style": "open-street-map",
                "layers": list_dict_circle
            })
    fig.update_layout(mapbox_style="open-street-map", height = 500)
    if path_plot == False:
        fig.show()
    else:
        fig.write_html(path_plot, auto_open = False)

In [49]:
def show_clients_terminals_150_outliers(df, dict_terminals, path_plot = False):
    dict_colors = {
        "No": "green",
        "Yes": "red",
        "Road": "blue"
    }
    list_dict_circle = [{
        "source": json.loads(
            poi_poly(None, poi={"Latitude": dict_terminals[i][0],"Longitude": dict_terminals[i][1]}, 
                     radius=150000).to_json()),
        "below": "traces",
        "type": "fill",
        "color": "green",
        "line": {"width": 1.5},
        "opacity": 0.2
        #"fillcolor": "red"
        } for i in dict_terminals.keys()]
    dict_points = create_dict_points(df, "Shipper name", "Shipper latitude", "Shipper longitude") 
    dict_points.update(create_dict_points(df, "Receiver name", "Receiver latitude", "Receiver longitude"))
    df_150_20 = create_df_analysis_150_20(df, dict_terminals, dict_points)
    df = df.merge(df_150_20[["More than 150km"]].reset_index(names = "Receiver name"), on = ["Receiver name"], how = "left")
    fig = go.Figure()
    df_temp = df[(df["More than 150km"]=="Yes")]
    fig.add_trace(go.Scattermapbox(lat=df_temp['Receiver latitude'].to_list(), lon=df_temp['Receiver longitude'].to_list(), 
                               mode = 'markers', marker = {'size': 4, 'color': "red"}, name = f"Clients with no suitable terminal",
                               customdata=df_temp[["Receiver name", "Sender weight (kg)"]],
                               hovertemplate='''<br>%{customdata[0]}: %{customdata[1]}kg<br><extra></extra>'''))
    fig.add_trace(go.Scattermapbox(lat=[i[0] for i in list(dict_terminals.values())], lon=[i[1] for i in list(dict_terminals.values())], 
                                   mode = 'markers', marker = {'size': 12, "color": "green"}, name = f"Terminals"))
    fig.update_layout(margin={"r": 0, "t": 40, "l": 0, "b": 40}, mapbox={
                      'zoom': 4, "center": {'lat': 45, 'lon': 3}})
    fig.update_layout(mapbox={
                "style": "open-street-map",
                "layers": list_dict_circle
            })
    fig.update_layout(legend=dict(
        yanchor="top",
        y=0.99,
        xanchor="left",
        x=0.01
    ))
    fig.update_layout(mapbox_style="open-street-map", height = 500)
    if path_plot == False:
        fig.show()
    else:
        fig.write_html(path_plot, auto_open = False)

In [50]:
show_terminals_150(dict_terminals, "output/plots/terminals_150.html")
show_clients_terminals_150_outliers(df, dict_terminals, "output/plots/clients_terminals_150_outliers.html")
show_clients_terminals_150(df_dc1, dict_terminals, "output/plots/clients_terminals_150.html")

C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\create_solution.py:122: FutureWarning:

Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.



(1626, 12)


NameError: name 'df_dc1' is not defined

****

In [ ]:
def plot_all_planning_horizons(df_plot):
    fig = make_subplots(rows=3, cols=2, shared_yaxes=True, horizontal_spacing=0.02, column_widths=[0.9, 0.1])
    i = 1
    df_plot["Planning date"] = df_plot["Delivery date"].dt.date
    df_grouped = df_plot.groupby(["Planning date"]).sum(numeric_only = True)
    title_xaxes = "Days"
    fig.add_trace(go.Bar(x = df_grouped.index, y=df_grouped["Sender weight (kg)"], 
                             hovertemplate='''<br>%{x}<br>Weight: %{y:,.0f} kg<br><extra></extra>'''),i, 1)
    fig.add_trace(go.Box(y=df_grouped[df_grouped["Sender weight (kg)"]>0]["Sender weight (kg)"],
                         customdata = df_grouped[df_grouped["Sender weight (kg)"]>0].index,
                        hovertemplate='''<br>%{customdata}<br>Weight: %{y:,.0f} kg<br><extra></extra>''', name = "Distribution"), i, 2)
    fig.update_yaxes(title = "sum of sender weight (kg)", col = 1, row = i)
    fig.update_xaxes(title = title_xaxes, col = 1, row = i)
    
    i = 2
    df_plot["Planning date"] = np.where(
                                (df_plot["Delivery date"].dt.weekday == 0)|
                                (df_plot["Delivery date"].dt.weekday == 1), "M", 
                                np.where(
                                    (df_plot["Delivery date"].dt.weekday == 2)|
                                    (df_plot["Delivery date"].dt.weekday == 3), "W", "F"))
    df_plot["Planning week"] = df_plot["Delivery date"].dt.isocalendar().week.astype(str)
    df_plot["Planning date"] = df_plot["Planning date"] + " W"+ df_plot["Planning week"]
    df_grouped = df_plot.groupby(["Planning date"]).sum(numeric_only = True)
    title_xaxes = "Days"
    fig.add_trace(go.Bar(x = df_grouped.index, y=df_grouped["Sender weight (kg)"], 
                             hovertemplate='''<br>%{x}<br>Weight: %{y:,.0f} kg<br><extra></extra>'''),i, 1)
    fig.add_trace(go.Box(y=df_grouped[df_grouped["Sender weight (kg)"]>0]["Sender weight (kg)"],
                         customdata = df_grouped[df_grouped["Sender weight (kg)"]>0].index,
                        hovertemplate='''<br>%{customdata}<br>Weight: %{y:,.0f} kg<br><extra></extra>''', name = "Distribution"), i, 2)
    fig.update_yaxes(title = "sum of sender weight (kg)", col = 1, row = i)
    fig.update_xaxes(title = title_xaxes, col = 1, row = i)
    fig.update_xaxes(categoryorder='array', categoryarray= list(df_plot["Planning date"].unique()), col = 1, row = i)
    
    i = 3
    df_plot["Planning date"] = df_plot["Delivery date"].dt.isocalendar().week
    df_grouped = df_plot.groupby(["Planning date"]).sum(numeric_only = True)
    title_xaxes = "Weeks"
    fig.add_trace(go.Bar(x = df_grouped.index, y=df_grouped["Sender weight (kg)"], 
                             hovertemplate='''<br>%{x}<br>Weight: %{y:,.0f} kg<br><extra></extra>'''),i, 1)
    fig.add_trace(go.Box(y=df_grouped[df_grouped["Sender weight (kg)"]>0]["Sender weight (kg)"],
                         customdata = df_grouped[df_grouped["Sender weight (kg)"]>0].index,
                        hovertemplate='''<br>%{customdata}<br>Weight: %{y:,.0f} kg<br><extra></extra>''', name = "Distribution"), i, 2)
    fig.update_yaxes(title = "sum of sender weight (kg)", col = 1, row = i)
    fig.update_xaxes(title = title_xaxes, col = 1, row = i)
    
    
    
    fig.update_layout(showlegend = False, height = 1000)
    fig.show()

In [ ]:
# Anhang
plot_all_planning_horizons(df_dc2)